# 그림데이터만 학습 (학습률 비교용)

In [1]:
# 라이브러리 불러오기
import os
import torch
import torch.nn as nn
from torch.utils.data import DataLoader, Dataset
from torchvision import transforms
from PIL import Image
import matplotlib.pyplot as plt
from transformers import (
    SwinForImageClassification, 
    SwinConfig,
    TrainingArguments, 
    Trainer,
    AutoImageProcessor,
    EarlyStoppingCallback
)

import numpy as np
from sklearn.metrics import accuracy_score
import json
import time
import psutil
import GPUtil

# GPU 설정
DEVICE = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"✅ 사용 디바이스: {DEVICE}")

# 경로 설정
DRAWING_DATA_PATH_TRAIN = "/workspace/datasets/dataset2yolo/drawing/train"
DRAWING_DATA_PATH_VAL = "/workspace/datasets/dataset2yolo/drawing/val"
DRAWING_ONLY_MODEL_PATH = "/workspace/models/drawing_only_swin"
TEST_FOLDER_PATH = "/workspace/testImg/val"  # 테스트 이미지 폴더 경로 설정

# 하이퍼파라미터
EPOCHS = 200
BATCH_SIZE = 32
IMG_SIZE = 224
LR = 1e-4
PATIENCE = 7

/workspace/.conda/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


✅ 사용 디바이스: cuda


In [ ]:
# 리소스 모니터링 클래스
class ResourceMonitor:
    def __init__(self):
        self.start_time = None
        self.gpu_stats = []
        self.cpu_stats = []
        self.memory_stats = []
        
    def start_monitoring(self):
        self.start_time = time.time()
        print("📊 리소스 모니터링 시작...")
        
    def log_resources(self, step_name=""):
        if self.start_time is None:
            return
            
        elapsed_time = time.time() - self.start_time
        
        # CPU 사용률
        cpu_percent = psutil.cpu_percent(interval=1)
        
        # 메모리 사용률
        memory = psutil.virtual_memory()
        memory_percent = memory.percent
        memory_used_gb = memory.used / (1024**3)
        
        # GPU 사용률 (GPU가 있을 경우)
        gpu_percent = 0
        gpu_memory_percent = 0
        if torch.cuda.is_available():
            try:
                gpus = GPUtil.getGPUs()
                if gpus:
                    gpu = gpus[0]
                    gpu_percent = gpu.load * 100
                    gpu_memory_percent = gpu.memoryUtil * 100
            except:
                pass
        
        stats = {
            'time': elapsed_time,
            'cpu_percent': cpu_percent,
            'memory_percent': memory_percent,
            'memory_used_gb': memory_used_gb,
            'gpu_percent': gpu_percent,
            'gpu_memory_percent': gpu_memory_percent,
            'step': step_name
        }
        
        self.cpu_stats.append(cpu_percent)
        self.memory_stats.append(memory_percent)
        self.gpu_stats.append(gpu_percent)
        
        if step_name:
            print(f"📊 {step_name} - CPU: {cpu_percent:.1f}%, RAM: {memory_percent:.1f}%, GPU: {gpu_percent:.1f}%")
        
        return stats
    
    def get_summary(self):
        if not self.cpu_stats:
            return {}
            
        return {
            'total_time': time.time() - self.start_time if self.start_time else 0,
            'avg_cpu': np.mean(self.cpu_stats),
            'max_cpu': np.max(self.cpu_stats),
            'avg_memory': np.mean(self.memory_stats),
            'max_memory': np.max(self.memory_stats),
            'avg_gpu': np.mean(self.gpu_stats) if self.gpu_stats else 0,
            'max_gpu': np.max(self.gpu_stats) if self.gpu_stats else 0
        }

class ImageClassificationDataset(Dataset):
    def __init__(self, data_path, processor, is_training=True):
        self.data_path = data_path
        self.processor = processor
        self.is_training = is_training
        
        # 클래스 폴더에서 이미지 경로와 라벨 수집
        self.images = []
        self.labels = []
        self.class_names = sorted(os.listdir(data_path))
        self.class_to_idx = {cls_name: idx for idx, cls_name in enumerate(self.class_names)}
        
        for class_name in self.class_names:
            class_path = os.path.join(data_path, class_name)
            if os.path.isdir(class_path):
                for img_name in os.listdir(class_path):
                    if img_name.lower().endswith(('.png', '.jpg', '.jpeg')):
                        self.images.append(os.path.join(class_path, img_name))
                        self.labels.append(self.class_to_idx[class_name])
        
        print(f"📊 데이터셋 정보 ({data_path}): {len(self.images)}개 이미지, {len(self.class_names)}개 클래스")
        print(f"📋 클래스: {self.class_names}")
    
    def __len__(self):
        return len(self.images)
    
    def __getitem__(self, idx):
        image_path = self.images[idx]
        label = self.labels[idx]
        
        # 이미지 로드
        image = Image.open(image_path).convert('RGB')
        
        # 전처리
        inputs = self.processor(image, return_tensors="pt")
        pixel_values = inputs['pixel_values'].squeeze(0)
        
        return {
            'pixel_values': pixel_values,
            'labels': torch.tensor(label, dtype=torch.long)
        }

def compute_metrics(eval_pred):
    predictions, labels = eval_pred
    predictions = np.argmax(predictions, axis=1)
    return {'accuracy': accuracy_score(labels, predictions)}

class ResourceTrackingTrainer(Trainer):
    def __init__(self, *args, resource_monitor=None, **kwargs):
        super().__init__(*args, **kwargs)
        self.resource_monitor = resource_monitor
        self.epoch_start_time = None
        
    def on_epoch_begin(self, args, state, control, **kwargs):
        self.epoch_start_time = time.time()
        if self.resource_monitor:
            self.resource_monitor.log_resources(f"Epoch {state.epoch} 시작")
    
    def on_epoch_end(self, args, state, control, **kwargs):
        if self.epoch_start_time and self.resource_monitor:
            epoch_time = time.time() - self.epoch_start_time
            self.resource_monitor.log_resources(f"Epoch {state.epoch} 완료 ({epoch_time:.1f}초)")

def create_trainer(model, train_dataset, eval_dataset, output_dir, epochs, learning_rate, resource_monitor=None):
    training_args = TrainingArguments(
        output_dir=output_dir,
        num_train_epochs=epochs,
        per_device_train_batch_size=BATCH_SIZE,
        per_device_eval_batch_size=BATCH_SIZE,
        learning_rate=learning_rate,
        weight_decay=0.01,
        logging_dir=f'{output_dir}/logs',
        logging_steps=10,
        eval_strategy="epoch",
        save_strategy="epoch",
        load_best_model_at_end=True,
        metric_for_best_model="accuracy",
        greater_is_better=True,
        save_total_limit=3,
        dataloader_num_workers=4,
        remove_unused_columns=False,
        push_to_hub=False,
        report_to=None,
    )
    
    trainer = ResourceTrackingTrainer(
        model=model,
        args=training_args,
        train_dataset=train_dataset,
        eval_dataset=eval_dataset,
        compute_metrics=compute_metrics,
        callbacks=[EarlyStoppingCallback(early_stopping_patience=PATIENCE)],
        resource_monitor=resource_monitor
    )
    
    return trainer

# 리소스 모니터 초기화
resource_monitor = ResourceMonitor()
resource_monitor.start_monitoring()

# 이미지 프로세서 초기화
processor = AutoImageProcessor.from_pretrained("microsoft/swin-base-patch4-window7-224")
resource_monitor.log_resources("프로세서 초기화 완료")

# 🎨 그림 데이터만으로 SWIN Transformer 학습
print("\n🎨 그림 데이터만으로 SWIN Transformer 학습")
print("=" * 60)

# 그림 데이터셋 생성 (train/val 분리)
drawing_train_dataset = ImageClassificationDataset(DRAWING_DATA_PATH_TRAIN, processor, is_training=True)
drawing_eval_dataset = ImageClassificationDataset(DRAWING_DATA_PATH_VAL, processor, is_training=False)
num_classes = len(drawing_train_dataset.class_names)

# 클래스 일치성 확인
if drawing_train_dataset.class_names != drawing_eval_dataset.class_names:
    print("⚠️  WARNING: Train과 Val 데이터셋의 클래스가 다릅니다!")
    print(f"Train classes: {drawing_train_dataset.class_names}")
    print(f"Val classes: {drawing_eval_dataset.class_names}")

resource_monitor.log_resources("데이터셋 로딩 완료")

# SWIN 모델 초기화 (사전훈련된 가중치 사용)
print(f"\n🧠 모델 초기화 (클래스 수: {num_classes})")
model_config = SwinConfig.from_pretrained("microsoft/swin-base-patch4-window7-224")
model_config.num_labels = num_classes
model = SwinForImageClassification.from_pretrained(
    "microsoft/swin-base-patch4-window7-224",
    config=model_config,
    ignore_mismatched_sizes=True
)

resource_monitor.log_resources("모델 초기화 완료")

# 모델 파라미터 수 출력
total_params = sum(p.numel() for p in model.parameters())
trainable_params = sum(p.numel() for p in model.parameters() if p.requires_grad)
print(f"📊 모델 파라미터:")
print(f"  - 총 파라미터: {total_params:,}")
print(f"  - 훈련 가능한 파라미터: {trainable_params:,}")
print(f"  - 훈련 가능한 비율: {trainable_params/total_params*100:.2f}%")

# Trainer 생성 및 학습
trainer = create_trainer(
    model, 
    drawing_train_dataset, 
    drawing_eval_dataset, 
    DRAWING_ONLY_MODEL_PATH,
    EPOCHS,
    LR,
    resource_monitor
)

# 학습 시작 시간 기록
training_start_time = time.time()
print(f"\n🚀 그림 데이터 학습 시작 (학습률: {LR})")
print(f"📊 학습 설정:")
print(f"  - 에포크: {EPOCHS}")
print(f"  - 배치 크기: {BATCH_SIZE}")
print(f"  - 이미지 크기: {IMG_SIZE}x{IMG_SIZE}")
print(f"  - 조기 종료 patience: {PATIENCE}")

# 학습 실행
trainer.train()
training_end_time = time.time()
training_duration = training_end_time - training_start_time

resource_monitor.log_resources("학습 완료")

# 모델 저장
trainer.save_model(DRAWING_ONLY_MODEL_PATH)
processor.save_pretrained(DRAWING_ONLY_MODEL_PATH)

# 클래스 정보 저장
class_info = {
    'class_names': drawing_train_dataset.class_names,
    'class_to_idx': drawing_train_dataset.class_to_idx,
    'num_classes': num_classes
}
with open(os.path.join(DRAWING_ONLY_MODEL_PATH, 'class_info.json'), 'w') as f:
    json.dump(class_info, f, indent=2)

print(f"📁 그림 전용 모델 저장 완료: {DRAWING_ONLY_MODEL_PATH}")

# 모델 평가
print("\n📊 최종 모델 평가")
final_results = trainer.evaluate()
print("🎯 최종 성능:")
for key, value in final_results.items():
    print(f"  {key}: {value:.4f}")

# 리소스 사용량 요약
resource_summary = resource_monitor.get_summary()
print(f"\n📊 리소스 사용량 요약:")
print(f"  - 총 학습 시간: {training_duration:.1f}초 ({training_duration/60:.1f}분)")
print(f"  - 평균 CPU 사용률: {resource_summary['avg_cpu']:.1f}%")
print(f"  - 최대 CPU 사용률: {resource_summary['max_cpu']:.1f}%")
print(f"  - 평균 메모리 사용률: {resource_summary['avg_memory']:.1f}%")
print(f"  - 최대 메모리 사용률: {resource_summary['max_memory']:.1f}%")
if resource_summary['avg_gpu'] > 0:
    print(f"  - 평균 GPU 사용률: {resource_summary['avg_gpu']:.1f}%")
    print(f"  - 최대 GPU 사용률: {resource_summary['max_gpu']:.1f}%")

# 학습 결과 저장
training_results = {
    'model_type': 'drawing_only',
    'training_duration': training_duration,
    'final_accuracy': final_results.get('eval_accuracy', 0),
    'final_loss': final_results.get('eval_loss', 0),
    'resource_usage': resource_summary,
    'hyperparameters': {
        'epochs': EPOCHS,
        'batch_size': BATCH_SIZE,
        'learning_rate': LR,
        'patience': PATIENCE
    },
    'model_info': {
        'total_params': total_params,
        'trainable_params': trainable_params,
        'num_classes': num_classes
    }
}

with open(os.path.join(DRAWING_ONLY_MODEL_PATH, 'training_results.json'), 'w') as f:
    json.dump(training_results, f, indent=2)

print("\n✅ 그림 전용 모델 학습이 완료되었습니다!")
print(f"📁 모델 저장 경로: {DRAWING_ONLY_MODEL_PATH}")
print(f"📊 학습 결과 저장: {os.path.join(DRAWING_ONLY_MODEL_PATH, 'training_results.json')}")

✅ 사용 디바이스: cuda
📊 리소스 모니터링 시작...


Using a slow image processor as `use_fast` is unset and a slow processor was saved with this model. `use_fast=True` will be the default behavior in v4.52, even if the model was saved with a slow processor. This will result in minor differences in outputs. You'll still be able to use a slow processor with `use_fast=False`.


📊 프로세서 초기화 완료 - CPU: 0.5%, RAM: 13.7%, GPU: 0.0%

🎨 그림 데이터만으로 SWIN Transformer 학습
📊 데이터셋 정보 (/workspace/datasets/dataset2yolo/drawing/train): 1522개 이미지, 4개 클래스
📋 클래스: ['angry', 'fear', 'happy', 'sad']
📊 데이터셋 정보 (/workspace/datasets/dataset2yolo/drawing/val): 469개 이미지, 4개 클래스
📋 클래스: ['angry', 'fear', 'happy', 'sad']
📊 데이터셋 로딩 완료 - CPU: 2.8%, RAM: 13.7%, GPU: 0.0%

🧠 모델 초기화 (클래스 수: 4)


Some weights of SwinForImageClassification were not initialized from the model checkpoint at microsoft/swin-base-patch4-window7-224 and are newly initialized because the shapes did not match:
- classifier.bias: found shape torch.Size([1000]) in the checkpoint and torch.Size([4]) in the model instantiated
- classifier.weight: found shape torch.Size([1000, 1024]) in the checkpoint and torch.Size([4, 1024]) in the model instantiated
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


📊 모델 초기화 완료 - CPU: 2.0%, RAM: 13.8%, GPU: 0.0%
📊 모델 파라미터:
  - 총 파라미터: 86,747,324
  - 훈련 가능한 파라미터: 86,747,324
  - 훈련 가능한 비율: 100.00%

🚀 그림 데이터 학습 시작 (학습률: 0.0001)
📊 학습 설정:
  - 에포크: 200
  - 배치 크기: 32
  - 이미지 크기: 224x224
  - 조기 종료 patience: 7


📊 학습 완료 - CPU: 0.4%, RAM: 14.0%, GPU: 0.0%
📁 그림 전용 모델 저장 완료: /workspace/models/drawing_only_swin

📊 최종 모델 평가


🎯 최종 성능:
  eval_loss: 0.4141
  eval_accuracy: 0.8891
  eval_runtime: 2.8597
  eval_samples_per_second: 164.0010
  eval_steps_per_second: 5.2450
  epoch: 12.0000

📊 리소스 사용량 요약:
  - 총 학습 시간: 354.3초 (5.9분)
  - 평균 CPU 사용률: 1.4%
  - 최대 CPU 사용률: 2.8%
  - 평균 메모리 사용률: 13.8%
  - 최대 메모리 사용률: 14.0%

✅ 그림 전용 모델 학습이 완료되었습니다!
📁 모델 저장 경로: /workspace/models/drawing_only_swin
📊 학습 결과 저장: /workspace/models/drawing_only_swin/training_results.json

🔍 테스트 결과 시각화
🔄 모델 로딩 중...
📊 12개 테스트 이미지 처리 중...
🎯 테스트 정확도: 1.0000 (12/12)



📋 상세 결과:
------------------------------------------------------------
✅  1. h98.jpeg             | Real: happy           | Pred: happy           | Conf: 0.9969
✅  2. new_a9.jpeg          | Real: angry           | Pred: angry           | Conf: 0.8161
✅  3. a16.jpg              | Real: angry           | Pred: angry           | Conf: 0.9970
✅  4. new_f13.jpeg         | Real: fear            | Pred: fear            | Conf: 0.9141
✅  5. new_f26.jpeg         | Real: fear            | Pred: fear            | Conf: 0.6532
✅  6. f103.jpeg            | Real: fear            | Pred: fear            | Conf: 0.6426
✅  7. a60.jpeg             | Real: angry           | Pred: angry           | Conf: 0.9982
✅  8. a27.jpg              | Real: angry           | Pred: angry           | Conf: 0.9994
✅  9. h69.jpg              | Real: happy           | Pred: happy           | Conf: 0.9995
✅ 10. a75.jpeg             | Real: angry           | Pred: angry           | Conf: 0.9469
✅ 11. new_h14.jpg          | 

In [4]:
# 테스트 이미지 시각화 함수
def visualize_test_results(model_path, test_folder_path, num_images=12):
    """
    테스트 폴더에서 이미지를 불러와서 예측 결과를 시각화
    """
    import random
    
    # 모델과 프로세서 로드
    print("🔄 모델 로딩 중...")
    model = SwinForImageClassification.from_pretrained(model_path)
    processor = AutoImageProcessor.from_pretrained(model_path)
    
    # 클래스 정보 로드
    with open(os.path.join(model_path, 'class_info.json'), 'r') as f:
        class_info = json.load(f)
    
    model.eval()
    model.to(DEVICE)
    
    # 테스트 이미지 수집
    test_images = []
    true_labels = []
    
    for class_name in os.listdir(test_folder_path):
        class_path = os.path.join(test_folder_path, class_name)
        if os.path.isdir(class_path):
            for img_name in os.listdir(class_path):
                if img_name.lower().endswith(('.png', '.jpg', '.jpeg')):
                    test_images.append(os.path.join(class_path, img_name))
                    true_labels.append(class_name)
    
    # 랜덤하게 선택
    if len(test_images) > num_images:
        selected_indices = random.sample(range(len(test_images)), num_images)
        test_images = [test_images[i] for i in selected_indices]
        true_labels = [true_labels[i] for i in selected_indices]
    
    print(f"📊 {len(test_images)}개 테스트 이미지 처리 중...")
    
    # 예측 수행
    predictions = []
    confidences = []
    
    for img_path in test_images:
        # 이미지 로드 및 전처리
        image = Image.open(img_path).convert('RGB')
        inputs = processor(image, return_tensors="pt").to(DEVICE)
        
        # 추론
        with torch.no_grad():
            outputs = model(**inputs)
            probs = torch.nn.functional.softmax(outputs.logits, dim=-1)
            pred_idx = torch.argmax(probs, dim=-1).item()
            confidence = probs[0][pred_idx].item()
            
            pred_class = class_info['class_names'][pred_idx]
            predictions.append(pred_class)
            confidences.append(confidence)
    
    # 정확도 계산
    correct = sum(1 for true, pred in zip(true_labels, predictions) if true == pred)
    accuracy = correct / len(true_labels)
    
    print(f"🎯 테스트 정확도: {accuracy:.4f} ({correct}/{len(true_labels)})")
    
    # 시각화
    fig, axes = plt.subplots(3, 4, figsize=(16, 12))
    fig.suptitle(f'Drawing-Only Model Test Results - Accuracy: {accuracy:.4f} ({correct}/{len(true_labels)})', 
                 fontsize=16, fontweight='bold')
    
    for i, (img_path, true_label, pred_label, conf) in enumerate(zip(test_images, true_labels, predictions, confidences)):
        if i >= 12:  # 최대 12개만 표시
            break
            
        row, col = i // 4, i % 4
        ax = axes[row, col]
        
        # 이미지 로드 및 표시
        image = Image.open(img_path).convert('RGB')
        ax.imshow(image)
        ax.axis('off')
        
        # 정답 여부에 따른 색상 설정
        color = 'green' if true_label == pred_label else 'red'
        
        # 라벨 텍스트 생성
        title = f"Real: {true_label}\nPred: {pred_label}\nConf: {conf:.3f}"
        ax.set_title(title, fontsize=10, color=color, fontweight='bold', pad=10)
        
        # 테두리 색상 설정
        for spine in ax.spines.values():
            spine.set_edgecolor(color)
            spine.set_linewidth(3)
    
    # 빈 subplot 숨기기
    for i in range(len(test_images), 12):
        row, col = i // 4, i % 4
        axes[row, col].axis('off')
    
    plt.tight_layout()
    plt.show()
    
    # 상세 결과 출력
    print("\n📋 상세 결과:")
    print("-" * 60)
    for i, (img_path, true_label, pred_label, conf) in enumerate(zip(test_images, true_labels, predictions, confidences)):
        status = "✅" if true_label == pred_label else "❌"
        img_name = os.path.basename(img_path)
        print(f"{status} {i+1:2d}. {img_name:20s} | Real: {true_label:15s} | Pred: {pred_label:15s} | Conf: {conf:.4f}")
    
    return accuracy, true_labels, predictions, confidences

# 테스트 실행
print("\n🔍 테스트 결과 시각화")
print("=" * 50)

# 테스트 폴더가 존재하는지 확인
if os.path.exists(TEST_FOLDER_PATH):
    accuracy, true_labels, predictions, confidences = visualize_test_results(
        DRAWING_ONLY_MODEL_PATH, 
        TEST_FOLDER_PATH, 
        num_images=12
    )
    
    # 클래스별 성능 분석
    from collections import defaultdict
    
    class_stats = defaultdict(lambda: {'correct': 0, 'total': 0})
    
    for true_label, pred_label in zip(true_labels, predictions):
        class_stats[true_label]['total'] += 1
        if true_label == pred_label:
            class_stats[true_label]['correct'] += 1
    
    print("\n📊 클래스별 성능:")
    print("-" * 40)
    for class_name, stats in class_stats.items():
        class_acc = stats['correct'] / stats['total'] if stats['total'] > 0 else 0
        print(f"{class_name:15s}: {class_acc:.4f} ({stats['correct']}/{stats['total']})")
    
else:
    print(f"❌ 테스트 폴더를 찾을 수 없습니다: {TEST_FOLDER_PATH}")

print(f"\n🎉 그림 전용 모델 학습 및 테스트 완료!")
print(f"📈 비교를 위해 training_results.json 파일을 확인하세요.")


🔍 테스트 결과 시각화
🔄 모델 로딩 중...


📊 12개 테스트 이미지 처리 중...
🎯 테스트 정확도: 0.5833 (7/12)



📋 상세 결과:
------------------------------------------------------------
❌  1. fear_14.jpg          | Real: fear            | Pred: sad             | Conf: 0.6453
❌  2. KakaoTalk_20250625_142209084_13.jpg | Real: happy           | Pred: angry           | Conf: 0.9896
❌  3. fear_6.jpg           | Real: fear            | Pred: angry           | Conf: 0.7597
✅  4. sad_32.jpg           | Real: sad             | Pred: sad             | Conf: 0.8253
✅  5. sad_10.jpg           | Real: sad             | Pred: sad             | Conf: 0.9165
❌  6. KakaoTalk_20250625_142209084_09.jpg | Real: happy           | Pred: angry           | Conf: 0.9910
✅  7. sad_30.jpg           | Real: sad             | Pred: sad             | Conf: 0.6220
✅  8. angry5.jpg           | Real: angry           | Pred: angry           | Conf: 0.9743
✅  9. angry7.jpg           | Real: angry           | Pred: angry           | Conf: 0.7022
❌ 10. KakaoTalk_20250625_142209084_15.jpg | Real: happy           | Pred: angry          